In [1]:
import django
import os
import pandas as pd
import numpy as np
import html
import namedentities as ne
from old_database.modules_webpage import entry_to_dict #read_publications, read_addresses, read_seminars
import time

os.environ.setdefault("DJANGO_SETTINGS_MODULE", "nanotud.settings")
from django.core.wsgi import get_wsgi_application
application = get_wsgi_application()
#from research.models import Publication


#from home.models import Room, Country, Title_full, Gender, Status
from internal.models import Member
from external.models import Conferencepresentation
#from teaching.models import Seminar

# needed when run inter jupyter enviornment:
os.environ["DJANGO_ALLOW_ASYNC_UNSAFE"] = "true"
django.setup()

#import gender_guesser.detector as gender
import re


## Write old papers database

In [2]:
def read_addresses(file_name):
    
    with open(file_name, 'r',encoding='utf-8',errors='replace') as file:
            content = file.read() 
    all_entries = content.split('enditem')
    
    for entry in all_entries:
        dictio = entry_to_dict(entry)
        if dictio != {}:
            try:
                df = df.append(dictio, ignore_index=True)     # append new entry to DF
            except:
                df = pd.DataFrame(dictio, index=[0])          # first time create the DF
    df = df.fillna(np.NaN)
    #ind = df[df['vorname'].isna() & df['nachname'].isna()].index.values
    #df.drop(ind,inplace=True)
    return df

In [3]:
path_presentation = 'old_database/database_mod.talks'
df_presentation = read_addresses(path_presentation)


In [4]:
df_presentation.columns

Index(['invited', 'type', 'nonmiei', 'host', 'year', 'month', 'day', 'where',
       'title', 'speaker', 'abstract', 'dayname', 'department', 'hostref',
       'hour', 'invitedby', 'invitedfor', 'speakerref', 'talkabstract', '',
       'und', 'room', 'molecular'],
      dtype='object')

**Write to Django Database**

In [5]:
for index, row in df_presentation.iterrows():
    no_speaker=False
    if type(row['year'])!= float: # or row['year']!='':
        year_raw=row['year']
        year_list=year_raw.split('-')
        year_start_raw=year_list[0]
        year_end_raw=year_list[-1]
    else:
        year_raw=None
    if type(row['month'])!=float: # or row['month']!='':
        month_raw=row['month']
        month_list=month_raw.split('-')
        month_start_raw=month_list[0]
        month_end_raw=month_list[-1]  
    else:
        month_start_raw='01'
        month_end_raw='01'
    if type(row['day'])!=float: # or row['days']!='':
        day_raw=row['day']
        day_list=day_raw.split('-')
        day_start_raw=day_list[0]
        day_end_raw=day_list[-1]
    else:
        day_start_raw='01'
        day_end_raw='01'
    if type(row['hour'])!=float: # or row['days']!='':
        try:
            int(row['hour'][0].strip())
            hour_raw=row['hour']
            hour_list=hour_raw.split('-')
            time_start_raw=hour_list[0].strip()
            time_end_raw=hour_list[-1].strip()
        except:
            time_start_raw=None
            time_end_raw=None
    else:
        time_start_raw=None
        time_end_raw=None
    public_raw=True
    if row['title']!=float:
        title_raw = html.unescape(row['title'])
    else:
        title_raw=None
    if type(row['nonmiei'])!=float:
        if row['nonmiei']=='no' or row['nonmiei']=='No' or row['nonmiei']=='NO':
            nonmiei_raw=False
        else:
            nonmiei_raw=True
    else:
        nonmiei_raw=False
    if type(row['hostref'])!=float:
        #copyright_raw=row['url']
        host_url_raw=row['hostref']
    else:
        host_url_raw=None
    if type(row['invitedby'])!=float:
        host_person_raw=html.unescape(row['invitedby'])
    else:
        host_person_raw=None
    if type(row['host'])!=float:
        host_university_raw=html.unescape(row['host'])
    else:
        host_university_raw=None
    if type(row['speaker'])!=float:
        try:
            idd = Member.objects.filter(last_name__icontains=row['speaker'].split(' ')[-1])[0].id
            speaker_raw = Member.objects.get(id=idd)
            print(idd,'SPEAKER',speaker_raw.id)
            speaker_char_raw=None
        except:
            no_speaker=True
            speaker_char_raw=row['speaker']
        # Presentation.add(speaker_raw.id)
        #speaker_char_raw=html.unescape(row['speaker'])
    else:
        speaker_char_raw=None
    if type(row['invitedfor'])!=float:
        event_title_raw=html.unescape(row['invitedfor'])
    else:
        event_title_raw=None
    if type(row['where'])!=float:
        location_raw=html.unescape(row['where'])
    else:
        location_raw=None
    if type(row['type'])!=float:
        event_type_raw=html.unescape(row['type'])
    else:
        event_type_raw=None
    if type(row['department'])!=float:
        host_department_raw=html.unescape(row['department'])
    else:
        host_department_raw=None
    if type(row['talkabstract'])!=float:
        abstract_raw=html.unescape(row['talkabstract'])
    elif type(row['abstract'])!=float:
        abstract_raw=html.unescape(row['abstract'])
    else:
        abstract_raw=None
    if type(row['room'])!=float:
        room_raw=html.unescape(row['room'])
    else:
        room_raw=None
    date_start_raw = f"{year_start_raw}-{month_start_raw}-{day_start_raw}"
    print('host_university_raw',host_university_raw)
    print('time_raw',time_start_raw,time_end_raw)
    print('date_start_raw',date_start_raw)
    print('title',title_raw)
    new_presentation = Presentation(    date=date_start_raw,
                          title=title_raw,
                            speaker_char=speaker_char_raw,
                            start_time=time_start_raw,
                            end_time=time_end_raw,
                          host_department=host_department_raw,
                            event_type=event_type_raw,
                            location=location_raw,
                            event_title=event_title_raw,
                            host_university=host_university_raw,
                            host_person=host_person_raw,
                            host_url=host_url_raw,
                          abstract=abstract_raw,
                            room=room_raw,
                            
                        )
   
    new_presentation.save()
    if not no_speaker:
        new_presentation.speaker.add(speaker_raw.id)
    time.sleep(0.25)

2429 SPEAKER 2429
host_university_raw UC Berkley
time_raw None None
date_start_raw 2019-08-12
title Reprogrammable materials
2429 SPEAKER 2429
host_university_raw The Shanghai Jiao Tong University
time_raw None None
date_start_raw 2019-05-16
title Materials 4.0: The age of cognitive materials
2429 SPEAKER 2429
host_university_raw Denmark University of Technology
time_raw None None
date_start_raw 2019-02-15
title Sensing at the quantum limit
2429 SPEAKER 2429
host_university_raw University of Jinan
time_raw None None
date_start_raw 2018-09-18
title Sensing towards the quantum limit: The convergence of molecular detection and artificial perceptrons
2429 SPEAKER 2429
host_university_raw TU Dresden
time_raw 14:30 14:50
date_start_raw 2018-05-04
title Cross-scale description of crack propagation in carbon fibre microstructures
2429 SPEAKER 2429
host_university_raw University of Sassari
time_raw 10:45 11:15
date_start_raw 2017-06-24
title Multifunctional biosensors for lab-on-a chip systems:

2429 SPEAKER 2429
host_university_raw Deutscher Akademischer Austausch Dienst DAAD
time_raw None None
date_start_raw 2013-05-24
title Aspect of the DE-KR Cooperation
2429 SPEAKER 2429
host_university_raw VolkswagenStiftung
time_raw None None
date_start_raw 2013-02-02
title Die Rolle der Universitätsreputation und der wissenschaftlichen Freiheit für die Karriereplanung von high-potential Nachwuchsforschern. Auf dem Weg vom \textit{First Author} zum \textit{Last Author}.
2429 SPEAKER 2429
host_university_raw International Iberian Nanotechnology Laboratory
time_raw None None
date_start_raw 2013-02-11
title Molecular nanostructures: growing mechanisms
2429 SPEAKER 2429
host_university_raw Friedrich-Schiller-Universität Jena
time_raw None None
date_start_raw 2013-01-25
title Thermoelectricity in molecular nanostructures: pros and pros
2429 SPEAKER 2429
host_university_raw Chalmers University of Technology
time_raw 13:15 13:15
date_start_raw 2012-10-29
title A molecular electronic route towa

2429 SPEAKER 2429
host_university_raw Fraunhofer Center Nanoelectronic Technology CNT in Dresden
time_raw 15:00 15:00
date_start_raw 2008-02-18
title Molecular nanoelectronics - the challenge for Si-based nanoelectronics? (<b>Fraunhofer CNT Kolloquium</b>)
2429 SPEAKER 2429
host_university_raw Max-Planck-Institut für Festkörperforschung, Stuttgart, Germany
time_raw 15:00 15:00
date_start_raw 2008-02-13
title Modeling molecular junctions: Pitfalls and caveats in understanding quantum transport mechanisms at the molecular scale
2442 SPEAKER 2442
host_university_raw Physics Department, New York University, USA
time_raw None None
date_start_raw 2007-11-01
title Biomimetic synthesis of advanced nanostructures
2442 SPEAKER 2442
host_university_raw Chemistry Department, New York University, USA
time_raw None None
date_start_raw 2007-11-01
title DNA- and protein-based hybrid nanostructures
2429 SPEAKER 2429
host_university_raw Royal Institute of Technology, Stockholm, Sweden
time_raw 10:00 10:

host_university_raw University of North Carolina at Chapel Hill, Chapel Hill, USA
time_raw 13:00 13:00
date_start_raw 2000-03-31
title The non-Fermi physics of electron transport in quantum wires
host_university_raw University of Mainz, Mainz, Germany
time_raw 10:15 10:15
date_start_raw 2000-01-21
title Challenges for physicists in finance and economics
host_university_raw Max Planck Institute for the Physics of Complex Systems,
time_raw 13:30 13:30
date_start_raw 1999-03-25
title Some aspects of nonlinear phenomena in novel electronic devices
host_university_raw Max Planck Institute of Colloids and Interfaces, Teltow,
time_raw None None
date_start_raw 1998-12-07
title Aspects of financial physics
host_university_raw Max Planck Institute for the Physics of Complex Systems,
time_raw None None
date_start_raw 1998-11-17
title Linear and nonlinear AC transport in quantum wires
host_university_raw University of Genoa, Genoa, Italy
time_raw None None
date_start_raw 1998-07-24
title Introduct

Old stuff:

In [ ]:
int('    ')